This is an implementation of the paper Deep Bayesian Active Learning with Image Data using PyTorch and modAL. 

modAL is an active learning framework for Python3, designed with modularity, flexibility and extensibility in mind. Built on top of scikit-learn, it allows you to rapidly create active learning workflows with nearly complete freedom. What is more, you can easily replace parts with your custom built solutions, allowing you to design novel algorithms with ease.

Since modAL only supports sklearn models, we will also use [skorch](https://skorch.readthedocs.io/en/stable/), a scikit-learn compatible neural network library that wraps PyTorch. 

In [1]:
import torch
import numpy as np
from torch import nn, optim
from torch.nn import functional as F
from torch.utils.data import DataLoader
from torchvision.transforms import ToTensor
from torchvision.datasets import CIFAR10
from skorch import NeuralNetClassifier
from modAL.models import ActiveLearner
from batchbald_redux import batchbald
from acquisition_functions import *
import os

In [2]:
import ssl
ssl._create_default_https_context = ssl._create_unverified_context

### architecture of the network we will be using

We will use the architecture described in the paper.

In [3]:
class MLP_REG(nn.Module):
    def __init__(self,):
        super(MLP_REG, self).__init__()
        self.layers = nn.Sequential(
            nn.Flatten(),
            nn.Linear(3072, 1024),
            nn.Dropout(p=0.25),
            nn.ReLU(),
            nn.Linear(1024, 512),
            nn.Dropout(p=0.25),
            nn.ReLU(),
            nn.Linear(512, 64),
            nn.Dropout(p=0.25),
            nn.ReLU(),
            nn.Linear(64, 64),
            nn.Dropout(p=0.25),
            nn.ReLU(),
            nn.Linear(64, 10),)
        
    def forward(self, x):
        return self.layers(x)


### read training data

In [4]:
dataset_train = CIFAR10('.', train=True, download=True, transform=ToTensor())
dataset_test  = CIFAR10('.', train=False,download=True, transform=ToTensor())

traindataloader = DataLoader(dataset_train, shuffle=True, batch_size=50000)
testdataloader  = DataLoader(dataset_test , shuffle=True, batch_size=10000)

X_train, y_train = next(iter(traindataloader))
X_test , y_test  = next(iter(testdataloader))


X_train = X_train.detach().numpy()
y_train = y_train.detach().numpy()

X_test = X_test.detach().numpy()
y_test = y_test.detach().numpy()


Files already downloaded and verified
Files already downloaded and verified


### preprocessing

### Active Learning Procedure

In [5]:
def active_learning_procedure(query_strategy,
                              X_test,
                              y_test,
                              X_pool,
                              y_pool,
                              X_initial,
                              y_initial,
                              estimator,
                              n_queries=198,
                              n_instances=10):
    learner = ActiveLearner(estimator=estimator,
                            X_training=X_initial,
                            y_training=y_initial,
                            query_strategy=query_strategy,
                           )
    perf_hist = [learner.score(X_test, y_test)]
    active_pool_size = [len(X_initial)]
    pool_size = len(X_initial)
    for index in range(n_queries):
        query_idx, query_instance = learner.query(X_pool, n_instances)
        learner.teach(X_pool[query_idx], y_pool[query_idx])
        X_pool = np.delete(X_pool, query_idx, axis=0)
        y_pool = np.delete(y_pool, query_idx, axis=0)
        model_accuracy = learner.score(X_test, y_test)
        pool_size = pool_size + n_instances
        print('Accuracy after query {n}: {acc:0.4f}'.format(n=index + 1, acc=model_accuracy))
        perf_hist.append(model_accuracy)
        active_pool_size.append(pool_size)
    return perf_hist, active_pool_size

In [6]:
results_path = 'results'

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

In [7]:
for exp_iter in range(5):
    np.random.seed(exp_iter)
    initial_idx = np.array([],dtype=int)
    for i in range(10):
        idx = np.random.choice(np.where(y_train==i)[0], size=2, replace=False)
        initial_idx = np.concatenate((initial_idx, idx))
    
    X_initial = X_train[initial_idx]
    y_initial = y_train[initial_idx]

    X_pool = np.delete(X_train, initial_idx, axis=0)
    y_pool = np.delete(y_train, initial_idx, axis=0)
    
    model = MLP_REG().to(device)

    estimator = NeuralNetClassifier(model,
                                  max_epochs=50,
                                  batch_size=128,
                                  lr=0.001,
                                  optimizer=torch.optim.Adam,
                                  criterion=torch.nn.CrossEntropyLoss,
                                  train_split=None,
                                  verbose=0,
                                  device=device)

    
    
    acc_arr, dataset_size_arr = active_learning_procedure(var_ratios,
                                                      X_test,
                                                      y_test,
                                                      X_pool,
                                                      y_pool,
                                                      X_initial,
                                                      y_initial,
                                                      estimator,)
    file_name = os.path.join(results_path, "var_ratios" + "_exp_" + str(exp_iter) + ".npy")
    np.save(file_name, (acc_arr, dataset_size_arr))
    
    X_initial = X_train[initial_idx]
    y_initial = y_train[initial_idx]

    X_pool = np.delete(X_train, initial_idx, axis=0)
    y_pool = np.delete(y_train, initial_idx, axis=0)
    
    model = MLP_REG().to(device)

    estimator = NeuralNetClassifier(model,
                                  max_epochs=50,
                                  batch_size=128,
                                  lr=0.001,
                                  optimizer=torch.optim.Adam,
                                  criterion=torch.nn.CrossEntropyLoss,
                                  train_split=None,
                                  verbose=0,
                                  device=device)

    acc_arr, dataset_size_arr = active_learning_procedure(mean_std,
                                                      X_test,
                                                      y_test,
                                                      X_pool,
                                                      y_pool,
                                                      X_initial,
                                                      y_initial,
                                                      estimator,)

    file_name = os.path.join(results_path, "mean_std" + "_exp_" + str(exp_iter) + ".npy")
    np.save(file_name, (acc_arr, dataset_size_arr))

    X_initial = X_train[initial_idx]
    y_initial = y_train[initial_idx]

    X_pool = np.delete(X_train, initial_idx, axis=0)
    y_pool = np.delete(y_train, initial_idx, axis=0)

    model = MLP_REG().to(device)
    
    estimator = NeuralNetClassifier(model,
                                  max_epochs=50,
                                  batch_size=128,
                                  lr=0.001,
                                  optimizer=torch.optim.Adam,
                                  criterion=torch.nn.CrossEntropyLoss,
                                  train_split=None,
                                  verbose=0,
                                  device=device)

    acc_arr, dataset_size_arr = active_learning_procedure(max_entropy,
                                                      X_test,
                                                      y_test,
                                                      X_pool,
                                                      y_pool,
                                                      X_initial,
                                                      y_initial,
                                                      estimator,)

    file_name = os.path.join(results_path, "max_entropy" + "_exp_" + str(exp_iter) + ".npy")
    np.save(file_name, (acc_arr, dataset_size_arr))

    X_initial = X_train[initial_idx]
    y_initial = y_train[initial_idx]

    X_pool = np.delete(X_train, initial_idx, axis=0)
    y_pool = np.delete(y_train, initial_idx, axis=0)
    
    model = MLP_REG().to(device)

    estimator = NeuralNetClassifier(model,
                                  max_epochs=50,
                                  batch_size=128,
                                  lr=0.001,
                                  optimizer=torch.optim.Adam,
                                  criterion=torch.nn.CrossEntropyLoss,
                                  train_split=None,
                                  verbose=0,
                                  device=device)

    acc_arr, dataset_size_arr = active_learning_procedure(bald,
                                                      X_test,
                                                      y_test,
                                                      X_pool,
                                                      y_pool,
                                                      X_initial,
                                                      y_initial,
                                                      estimator,)

    file_name = os.path.join(results_path, "bald" + "_exp_" + str(exp_iter) + ".npy")
    np.save(file_name, (acc_arr, dataset_size_arr))

    X_initial = X_train[initial_idx]
    y_initial = y_train[initial_idx]

    X_pool = np.delete(X_train, initial_idx, axis=0)
    y_pool = np.delete(y_train, initial_idx, axis=0)
    
    model = MLP_REG().to(device)

    estimator = NeuralNetClassifier(model,
                                  max_epochs=50,
                                  batch_size=128,
                                  lr=0.001,
                                  optimizer=torch.optim.Adam,
                                  criterion=torch.nn.CrossEntropyLoss,
                                  train_split=None,
                                  verbose=0,
                                  device=device)

    acc_arr, dataset_size_arr = active_learning_procedure(uniform,
                                                      X_test,
                                                      y_test,
                                                      X_pool,
                                                      y_pool,
                                                      X_initial,
                                                      y_initial,
                                                      estimator,)

    file_name = os.path.join(results_path, "uniform" + "_exp_" + str(exp_iter) + ".npy")
    np.save(file_name, (acc_arr, dataset_size_arr))

    X_initial = X_train[initial_idx]
    y_initial = y_train[initial_idx]

    X_pool = np.delete(X_train, initial_idx, axis=0)
    y_pool = np.delete(y_train, initial_idx, axis=0)
    
    model = MLP_REG().to(device)

    estimator = NeuralNetClassifier(model,
                                  max_epochs=50,
                                  batch_size=128,
                                  lr=0.001,
                                  optimizer=torch.optim.Adam,
                                  criterion=torch.nn.CrossEntropyLoss,
                                  train_split=None,
                                  verbose=0,
                                  device=device)

    acc_arr, dataset_size_arr = active_learning_procedure(batch_bald,
                                                      X_test,
                                                      y_test,
                                                      X_pool,
                                                      y_pool,
                                                      X_initial,
                                                      y_initial,
                                                      estimator,)

    file_name = os.path.join(results_path, "batch_bald" + "_exp_" + str(exp_iter) + ".npy")
    np.save(file_name, (acc_arr, dataset_size_arr))
  

Accuracy after query 1: 0.1869
Accuracy after query 2: 0.1879
Accuracy after query 3: 0.1912
Accuracy after query 4: 0.2035
Accuracy after query 5: 0.2160
Accuracy after query 6: 0.2089
Accuracy after query 7: 0.2129
Accuracy after query 8: 0.2155
Accuracy after query 9: 0.2206
Accuracy after query 10: 0.2381
Accuracy after query 11: 0.2353
Accuracy after query 12: 0.2518
Accuracy after query 13: 0.2487
Accuracy after query 14: 0.2687
Accuracy after query 15: 0.2639
Accuracy after query 16: 0.2663
Accuracy after query 17: 0.2721
Accuracy after query 18: 0.2711
Accuracy after query 19: 0.2788
Accuracy after query 20: 0.2770
Accuracy after query 21: 0.2830
Accuracy after query 22: 0.2755
Accuracy after query 23: 0.2849
Accuracy after query 24: 0.2863
Accuracy after query 25: 0.2902
Accuracy after query 26: 0.2936
Accuracy after query 27: 0.2981
Accuracy after query 28: 0.2951
Accuracy after query 29: 0.2990
Accuracy after query 30: 0.2899
Accuracy after query 31: 0.3008
Accuracy after qu

Accuracy after query 57: 0.2816
Accuracy after query 58: 0.2830
Accuracy after query 59: 0.2868
Accuracy after query 60: 0.2850
Accuracy after query 61: 0.2841
Accuracy after query 62: 0.2798
Accuracy after query 63: 0.2988
Accuracy after query 64: 0.2783
Accuracy after query 65: 0.2873
Accuracy after query 66: 0.2899
Accuracy after query 67: 0.2778
Accuracy after query 68: 0.2996
Accuracy after query 69: 0.2920
Accuracy after query 70: 0.2923
Accuracy after query 71: 0.2934
Accuracy after query 72: 0.3015
Accuracy after query 73: 0.2991
Accuracy after query 74: 0.2995
Accuracy after query 75: 0.3049
Accuracy after query 76: 0.3064
Accuracy after query 77: 0.2952
Accuracy after query 78: 0.3037
Accuracy after query 79: 0.2821
Accuracy after query 80: 0.3094
Accuracy after query 81: 0.2998
Accuracy after query 82: 0.2891
Accuracy after query 83: 0.3036
Accuracy after query 84: 0.3000
Accuracy after query 85: 0.3173
Accuracy after query 86: 0.2956
Accuracy after query 87: 0.2976
Accuracy

Accuracy after query 112: 0.3022
Accuracy after query 113: 0.2973
Accuracy after query 114: 0.3020
Accuracy after query 115: 0.3102
Accuracy after query 116: 0.3020
Accuracy after query 117: 0.2972
Accuracy after query 118: 0.3073
Accuracy after query 119: 0.2970
Accuracy after query 120: 0.3001
Accuracy after query 121: 0.3003
Accuracy after query 122: 0.3035
Accuracy after query 123: 0.2937
Accuracy after query 124: 0.2937
Accuracy after query 125: 0.3075
Accuracy after query 126: 0.3023
Accuracy after query 127: 0.3066
Accuracy after query 128: 0.3092
Accuracy after query 129: 0.3030
Accuracy after query 130: 0.3056
Accuracy after query 131: 0.3005
Accuracy after query 132: 0.3073
Accuracy after query 133: 0.3081
Accuracy after query 134: 0.3134
Accuracy after query 135: 0.3109
Accuracy after query 136: 0.3155
Accuracy after query 137: 0.3129
Accuracy after query 138: 0.3197
Accuracy after query 139: 0.3215
Accuracy after query 140: 0.3133
Accuracy after query 141: 0.3147
Accuracy a

Accuracy after query 166: 0.3102
Accuracy after query 167: 0.3028
Accuracy after query 168: 0.3093
Accuracy after query 169: 0.3097
Accuracy after query 170: 0.3106
Accuracy after query 171: 0.3217
Accuracy after query 172: 0.3160
Accuracy after query 173: 0.3246
Accuracy after query 174: 0.3235
Accuracy after query 175: 0.3040
Accuracy after query 176: 0.3165
Accuracy after query 177: 0.3137
Accuracy after query 178: 0.3321
Accuracy after query 179: 0.3267
Accuracy after query 180: 0.3211
Accuracy after query 181: 0.3241
Accuracy after query 182: 0.3154
Accuracy after query 183: 0.3255
Accuracy after query 184: 0.3232
Accuracy after query 185: 0.3212
Accuracy after query 186: 0.3221
Accuracy after query 187: 0.3253
Accuracy after query 188: 0.3301
Accuracy after query 189: 0.3225
Accuracy after query 190: 0.3323
Accuracy after query 191: 0.3237
Accuracy after query 192: 0.3213
Accuracy after query 193: 0.3112
Accuracy after query 194: 0.3274
Accuracy after query 195: 0.3277
Accuracy a

Conditional Entropy:   0%|          | 0/2000 [00:00<?, ?it/s]

...

SampledJointEntropy.compute_batch:   0%|          | 0/2000 [00:00<?, ?it/s]

SampledJointEntropy.compute_batch:   0%|          | 0/2000 [00:00<?, ?it/s]

SampledJointEntropy.compute_batch:   0%|          | 0/2000 [00:00<?, ?it/s]

SampledJointEntropy.compute_batch:   0%|          | 0/2000 [00:00<?, ?it/s]

Accuracy after query 198: 0.2966
